<a href="https://www.kaggle.com/code/galvangoh/melbourne-housing-dataset?scriptVersionId=104025427" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

***
# Melbourne Housing Price Dataset
***
## Regression Problem
***
#### [Melbourne house pricing](https://www.kaggle.com/dansbecker/melbourne-housing-snapshot/home "Click to see the source from Kaggle")
****

#### Notes on Specific Variables
---

>Rooms: Number of rooms

>Price: Price in dollars

>Method: S - property sold; SP - property sold prior; PI - property passed in; PN - sold prior not disclosed; SN - sold not disclosed; NB - no bid; VB - vendor bid; W - withdrawn prior to auction; SA - sold after auction; SS - sold after auction price not disclosed. N/A - price or highest bid not available.

>Type: br - bedroom(s); h - house, cottage, villa, semi, terrace; u - unit, duplex; t - townhouse; dev site - development site; o res - other residential.

>SellerG: Real Estate Agent

>Date: Date sold

>Distance: Distance from CBD

>Regionname: General Region (West, North West, North, North east …etc)

>Propertycount: Number of properties that exist in the suburb.

>Bedroom2 : Scraped # of Bedrooms (from different source)

>Bathroom: Number of Bathrooms

>Car: Number of carspots

>Landsize: Land Size

>BuildingArea: Building Size

>CouncilArea: Governing council for the area

# A. Libraries needed for this study

In [1]:
# for working with dataframes
import pandas as pd
from sklearn import preprocessing
import numpy as np

# for visualisation
import plotly.express as px

# hide any warnings from output
import warnings
warnings.filterwarnings("ignore")

# notebook settings
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

# 1. Data Preparation

## 1.1. Importing dataset

In [2]:
# set pandas to display all columns of data
pd.set_option('display.max_columns', None)

# read in the data
melb_house_price_df = pd.read_csv('../input/melb-housing-dataset/melb_data.csv')

## 1.2. High level look at the dataset

In [3]:
melb_house_price_df.head()

Suburb           Address  Rooms Type    Price Method SellerG     Date  \
0  Abbotsford      85 Turner St      2    h  1480000      S     NaN  3/12/16   
1  Abbotsford   25 Bloomburg St      2    h  1035000      S  Biggin   4/2/16   
2  Abbotsford      5 Charles St      3    h  1465000     SP  Biggin   4/3/17   
3  Abbotsford  40 Federation La      3    h   850000     PI  Biggin   4/3/17   
4  Abbotsford       55a Park St      4    h  1600000     VB  Nelson   4/6/16   

   Distance  Postcode  Bedroom2  Bathroom  Car  Landsize  BuildingArea  \
0       2.5      3067         2         1  1.0       202           NaN   
1       2.5      3067         2         1  0.0       156          79.0   
2       2.5      3067         3         2  0.0       134         150.0   
3       2.5      3067         3         2  1.0        94           NaN   
4       2.5      3067         3         1  2.0       120         142.0   

   YearBuilt CouncilArea  Lattitude  Longtitude             Regionname  \
0        NaN       Yarra   -37.7996    144.9984  Northern Metropolitan   
1     1900.0       Yarra   -37.8079    144.9934  Northern Metropolitan   
2     1900.0       Yarra   -37.8093    144.9944  Northern Metropolitan   
3        NaN       Yarra   -37.7969    144.9969  Northern Metropolitan   
4     2014.0       Yarra   -37.8072    144.9941  Northern Metropolitan   

   Propertycount  
0           4019  
1           4019  
2           4019  
3           4019  
4           4019

In [4]:
melb_house_price_df.shape

(13580, 21)

13580 rows and 21 columns of data

In [5]:
melb_house_price_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13580 entries, 0 to 13579
Data columns (total 21 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Suburb         13580 non-null  object 
 1   Address        13580 non-null  object 
 2   Rooms          13580 non-null  int64  
 3   Type           13580 non-null  object 
 4   Price          13580 non-null  int64  
 5   Method         13580 non-null  object 
 6   SellerG        13579 non-null  object 
 7   Date           13580 non-null  object 
 8   Distance       13580 non-null  float64
 9   Postcode       13580 non-null  int64  
 10  Bedroom2       13580 non-null  int64  
 11  Bathroom       13580 non-null  int64  
 12  Car            13518 non-null  float64
 13  Landsize       13580 non-null  int64  
 14  BuildingArea   7130 non-null   float64
 15  YearBuilt      8205 non-null   float64
 16  CouncilArea    12211 non-null  object 
 17  Lattitude      13580 non-null  float64
 18  Longti

In [6]:
melb_house_price_df.describe().T

count          mean            std          min  \
Rooms          13580.0  2.937997e+00       0.955748      1.00000   
Price          13580.0  1.075684e+06  639310.724296  85000.00000   
Distance       13580.0  1.013778e+01       5.868725      0.00000   
Postcode       13580.0  3.105302e+03      90.676964   3000.00000   
Bedroom2       13580.0  2.914728e+00       0.965921      0.00000   
Bathroom       13580.0  1.534242e+00       0.691712      0.00000   
Car            13518.0  1.610075e+00       0.962634      0.00000   
Landsize       13580.0  5.584161e+02    3990.669241      0.00000   
BuildingArea    7130.0  1.519676e+02     541.014538      0.00000   
YearBuilt       8205.0  1.964684e+03      37.273762   1196.00000   
Lattitude      13580.0 -3.780920e+01       0.079260    -38.18255   
Longtitude     13580.0  1.449952e+02       0.103916    144.43181   
Propertycount  13580.0  7.454417e+03    4378.581772    249.00000   

                         25%            50%           75%           max  
Rooms               2.000000       3.000000  3.000000e+00  1.000000e+01  
Price          650000.000000  903000.000000  1.330000e+06  9.000000e+06  
Distance            6.100000       9.200000  1.300000e+01  4.810000e+01  
Postcode         3044.000000    3084.000000  3.148000e+03  3.977000e+03  
Bedroom2            2.000000       3.000000  3.000000e+00  2.000000e+01  
Bathroom            1.000000       1.000000  2.000000e+00  8.000000e+00  
Car                 1.000000       2.000000  2.000000e+00  1.000000e+01  
Landsize          177.000000     440.000000  6.510000e+02  4.330140e+05  
BuildingArea       93.000000     126.000000  1.740000e+02  4.451500e+04  
YearBuilt        1940.000000    1970.000000  1.999000e+03  2.018000e+03  
Lattitude         -37.856822     -37.802355 -3.775640e+01 -3.740853e+01  
Longtitude        144.929600     145.000100  1.450583e+02  1.455264e+02  
Propertycount    4380.000000    6555.000000  1.033100e+04  2.165000e+04

## 1.3. Split datatframe into numerical and categorical dataframes

In [7]:
# find out the number of columns which are categorical
num_col = melb_house_price_df.select_dtypes(exclude='object')

# find out the number of columns which are numerical
cat_col = melb_house_price_df.select_dtypes(exclude=['int64','float64'])

print(f"There are {num_col.shape[1]} numerical features.")
print(f"\nThere are {cat_col.shape[1]} categorical features.")

There are 13 numerical features.

There are 8 categorical features.


### 1.3.1. Finding numerical features with correlation with outcome

In [8]:
# create a new variable to contain only the numerical features of the dataset
num_col_corr = num_col.corr()

# create a heatmap of all numerical features and outcome
num_col_heatmap = px.imshow(num_col_corr, height = 700, width = 700,
                            title = "Heatmap Correlation for Numerical Features")

num_col_heatmap.show()

Here, we can see some of the numerical features having some correlation with Price:
1. Rooms
2. Bedroom2
3. Bathroom

### 1.3.2. Look at the relationship between categorical features and outcome

In [9]:
# add in the outcome column into cat_col
cat_col["Price"] = melb_house_price_df["Price"]

cat_col_df = px.scatter_matrix(cat_col, height = 900, width = 900)

cat_col_df.show()

Even though not much inference can be made at this stage, there is some minor observations made:
1. Different suburbs have different housing price.
2. h Type house tends to be sold at a higher price (higher grade house).
3. Specific council area affects housing price.
4. Different regions have different housing price.

# 2. Exploratory Data Analysis

## 2.1. Undertstanding features of this dataset

### 2.1.1 Suburb

#### Suburb refers to city within Melbourne where citizens find residence and it is also an area where businesses and government organisations are located.

#### Here we see how many are there in terms of property sales method

In [10]:
# Find the suburb with the highest sales in house price
suburb_highest_price = melb_house_price_df.groupby(by="Suburb").sum()[["Price"]].sort_values(by="Price", ascending=False)
suburb_highest_price.reset_index(inplace=True)
suburb_highest_price

Suburb      Price
0         Brighton  359009388
1        Glen Iris  316844500
2              Kew  311243000
3     Balwyn North  306672300
4         Richmond  281726750
..             ...        ...
309   Bullengarook     535000
310     Brookfield     456000
311         Wallan     366000
312       Rockbank     340000
313  Bacchus Marsh     285000

[314 rows x 2 columns]

In [11]:
# design the box plot
fig_suburb = px.histogram(suburb_highest_price, x="Suburb", y="Price",
                          log_y=True, width=5000, height=700,
                          orientation='v', title="Property Sales History for all Suburbs")

# display the plot
fig_suburb.show()

<b>Suburb with the highest property sales</b> -> Brighton<br>
<b>Suburb with the lowest property sales</b> -> Bacchus Marsh

#### Here we try to see the range of house prices across all cities in this dataset.

In [12]:
# create a new dataframe for the pivot table
suburb_sum_price = melb_house_price_df.pivot_table(index="Suburb", columns="Type", aggfunc=("min","max","sum"))["Price"]

# sort the dataframe # swap the level 1 and level 2 in the tuple to look at different price ranges
suburb_sum_price= suburb_sum_price.sort_values(by=[("min","u")], ascending=False)

# display the dataframe
suburb_sum_price

max                             min             \
Type                      h          t         u          h          t   
Suburb                                                                   
McKinnon          2300000.0  1655000.0  960000.0  1200000.0  1125000.0   
Doncaster East    1890000.0  1500000.0  871000.0  1120000.0   816000.0   
Notting Hill      1211000.0        NaN  840000.0  1075000.0        NaN   
Bulleen           1751000.0  1250000.0  860000.0   760000.0   599900.0   
Strathmore        2650000.0   995000.0  750000.0   535000.0   600000.0   
...                     ...        ...       ...        ...        ...   
Williams Landing   555000.0        NaN       NaN   510000.0        NaN   
Wonga Park         900000.0        NaN       NaN   900000.0        NaN   
Wyndham Vale       500000.0        NaN       NaN   475000.0        NaN   
Yallambie         1670000.0        NaN       NaN   602500.0        NaN   
Yarra Glen         620000.0        NaN       NaN   620000.0        NaN   

                                   sum                        
Type                     u           h          t          u  
Suburb                                                        
McKinnon          960000.0   8260000.0  2780000.0   960000.0  
Doncaster East    850000.0  49461000.0  5581000.0  1721000.0  
Notting Hill      840000.0   2286000.0        NaN   840000.0  
Bulleen           787000.0  74034000.0  4684900.0  3310500.0  
Strathmore        750000.0  71665500.0  2520000.0   750000.0  
...                    ...         ...        ...        ...  
Williams Landing       NaN   1065000.0        NaN        NaN  
Wonga Park             NaN    900000.0        NaN        NaN  
Wyndham Vale           NaN   1933000.0        NaN        NaN  
Yallambie              NaN  20152500.0        NaN        NaN  
Yarra Glen             NaN    620000.0        NaN        NaN  

[314 rows x 9 columns]

### 2.1.2 Method

#### Kaggle provided a few acroynms however only 5 methods were known in this dataset.

S - property sold - [what does it mean](https://upside.com.au/articles/selling-your-property/selling-guide/common-real-estate-terms-and-definitions-explained)<br>
SP - property sold prior - [what does it mean?](https://www.therealestateconversation.com.au/blog/justin-nickerson/why-would-you-sell-property-prior-auction/justin-nickerson-auctioneer/justin)<br>
PI - property passed in - [what does it mean?](https://www.greghocking.com.au/what-happens-if-a-property-is-passed-in-at-auction/#:~:text=When%20a%20property%20is%20passed,crowd%20or%20a%20vendor%20bid.)<br>
VB - vendor bid - [what does it mean?](https://www.realestate.com.au/advice/auction-hammer-falls-vendor-bid/)<br>
SA - sold after auction - [what does it mean?](https://www.domain.com.au/advice/the-block-2018-how-auctions-work-in-victoria-777537/)

#### Here we find out all different types of property sales methods

In [13]:
# group the dataframe by the sales methods
melb_house_price_df.groupby(by="Method").count()

Suburb  Address  Rooms  Type  Price  SellerG  Date  Distance  \
Method                                                                 
PI        1564     1564   1564  1564   1564     1564  1564      1564   
S         9022     9022   9022  9022   9022     9021  9022      9022   
SA          92       92     92    92     92       92    92        92   
SP        1703     1703   1703  1703   1703     1703  1703      1703   
VB        1199     1199   1199  1199   1199     1199  1199      1199   

        Postcode  Bedroom2  Bathroom   Car  Landsize  BuildingArea  YearBuilt  \
Method                                                                          
PI          1564      1564      1564  1557      1564           870        995   
S           9022      9022      9022  8988      9022          4568       5271   
SA            92        92        92    91        92            44         50   
SP          1703      1703      1703  1695      1703          1012       1136   
VB          1199      1199      1199  1187      1199           636        753   

        CouncilArea  Lattitude  Longtitude  Regionname  Propertycount  
Method                                                                 
PI             1416       1564        1564        1564           1564  
S              8111       9022        9022        9022           9022  
SA               81         92          92          92             92  
SP             1536       1703        1703        1703           1703  
VB             1067       1199        1199        1199           1199

Focusing on the features without null values such as "Price";<br>
Sales method <b>"S" (Property Sold)</b> is the most common between home owners and home sellers.<br>
<b>"SA" (Sold After Auction)</b> is the least common sales method.

#### Visualise the total amount of sales by each method

In [14]:
# design the bar plot to show the sum of property prices differentiated by sales method
fig_method = px.histogram(melb_house_price_df, x="Price", y="Method",
                          color="Type", title="Total Amount of Sales by Method")

# display the plot
fig_method.show()

- Method by Property Sold is a clear winner here.

- It can be also observed that property type "h" had won the hearts of many buyers. Property type "h" always have the highest sales amount no matter the sales method.

- [This article](https://lawyersconveyancing.com.au/faq/auctions-faq/) explains why other sale methods were not gaining much sales as Property Sold.

### 2.1.3 Distance

#### This feature should be intuitive for most of us. Distance here means the distance between the property and CBD. So it it only natural that the lower the distance, the higher the sales price.

In [15]:
# labeling for the plot
labels = {"Price":"House Price",
          "Distance":"Distance to CBD (Km)"} # many kagglers have used kilometers as the metric

# design the plot to show the effects on property prices when distance matters
fig_house_dist_price = px.scatter(melb_house_price_df, x="Distance", y="Price",
                                  facet_col="Type", log_y=True, trendline="ols",
                                  title="House Prices w.r.t. Distance to CBD", marginal_x="box",
                                  height=600, labels=labels, trendline_color_override="black")
fig_house_dist_price.show()

- Ignore the outliers first and look at the trendline, the higher the distance to CBD, the lower the house prices.
- Majority of the properties are located within 20 Km of CBD.
- For properties located above 20 Km of CBD, property type "h" has higher proportion as compared to type "u" and "t". Probably for property owners whom want peace from the buzzling city.

### 2.1.4 Geographical features

#### Similarly with Distance, geograhical features of the properties should also affect property prices. With the knowledge of a list of places of interest around the Postcode, Latitude and Longtitude, some feature engineering can be perform.

In [16]:
# create a new dataframe to hold all the geograhical features
geo_features_df = melb_house_price_df[["Postcode", "CouncilArea", "Lattitude", "Longtitude", "Price"]]
geo_features_df.head()

Postcode CouncilArea  Lattitude  Longtitude    Price
0      3067       Yarra   -37.7996    144.9984  1480000
1      3067       Yarra   -37.8079    144.9934  1035000
2      3067       Yarra   -37.8093    144.9944  1465000
3      3067       Yarra   -37.7969    144.9969   850000
4      3067       Yarra   -37.8072    144.9941  1600000

#### Create a new column to show the different group of pricing

In [17]:
# cut the range of property price into 10 groups and create a new column for it
geo_features_df["Price_Group"] = pd.cut(geo_features_df["Price"], bins=10)
geo_features_df

# show all 10 different price group
geo_features_df.Price_Group.value_counts().sort_values(ascending=False)

Postcode CouncilArea  Lattitude  Longtitude    Price  \
0          3067       Yarra  -37.79960   144.99840  1480000   
1          3067       Yarra  -37.80790   144.99340  1035000   
2          3067       Yarra  -37.80930   144.99440  1465000   
3          3067       Yarra  -37.79690   144.99690   850000   
4          3067       Yarra  -37.80720   144.99410  1600000   
...         ...         ...        ...         ...      ...   
13575      3150         NaN  -37.90562   145.16761  1245000   
13576      3016         NaN  -37.85927   144.87904  1031000   
13577      3016         NaN  -37.85274   144.88738  1170000   
13578      3016         NaN  -37.85908   144.89299  2500000   
13579      3013         NaN  -37.81188   144.88449  1285000   

                  Price_Group  
0       (976500.0, 1868000.0]  
1       (976500.0, 1868000.0]  
2       (976500.0, 1868000.0]  
3         (76085.0, 976500.0]  
4       (976500.0, 1868000.0]  
...                       ...  
13575   (976500.0, 1868000.0]  
13576   (976500.0, 1868000.0]  
13577   (976500.0, 1868000.0]  
13578  (1868000.0, 2759500.0]  
13579   (976500.0, 1868000.0]  

[13580 rows x 6 columns]

(76085.0, 976500.0]       7573
(976500.0, 1868000.0]     4693
(1868000.0, 2759500.0]     982
(2759500.0, 3651000.0]     239
(3651000.0, 4542500.0]      62
(4542500.0, 5434000.0]      17
(5434000.0, 6325500.0]       9
(6325500.0, 7217000.0]       2
(7217000.0, 8108500.0]       2
(8108500.0, 9000000.0]       1
Name: Price_Group, dtype: int64

#### Reassign each price group with a number in a way as the number of price group increase, so does the price of the property.

In [18]:
# using label encoder to do the reassignment
le = preprocessing.LabelEncoder()

# changing the price_group values to categorial so that plotly will display them as discreate colors rather than continous
geo_features_df["Price_Group"] = le.fit_transform(geo_features_df["Price_Group"]).astype(str)

In [19]:
# check if the label encoders works
geo_features_df.Price_Group.value_counts().sort_values(ascending=False)

# check dtype of price group
geo_features_df.info()

0    7573
1    4693
2     982
3     239
4      62
5      17
6       9
7       2
8       2
9       1
Name: Price_Group, dtype: int64

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13580 entries, 0 to 13579
Data columns (total 6 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   Postcode     13580 non-null  int64  
 1   CouncilArea  12211 non-null  object 
 2   Lattitude    13580 non-null  float64
 3   Longtitude   13580 non-null  float64
 4   Price        13580 non-null  int64  
 5   Price_Group  13580 non-null  object 
dtypes: float64(2), int64(2), object(2)
memory usage: 636.7+ KB


In [20]:
# setting the price legend
price_legend = {"0":"< 0.976",
                "1":"0.976 - 1.868",
                "2":"1.868 - 2.759",
                "3":"2.759 - 3.651",
                "4":"3.651 - 4.542",
                "5":"4.542 - 5.434",
                "6":"5.434 - 6.325",
                "7":"6.325 - 7.217",
                "8":"7.217 - 8.108",
                "9":"8.108 - 9.000"}

# edit the labels
labels = {"Price_Group":"Prices in $ Million"}

# design the geographical plot
geo_fig = px.scatter_mapbox(geo_features_df, lat="Lattitude", lon="Longtitude",
                            hover_name="CouncilArea", zoom=10, color="Price_Group",
                            height=800, width=1000, labels=labels,
                            category_orders = {"Price_Group":["0","1","2","3","4","5","6","7","8","9"]},
                            title="Property Price and Location In Melbourne",
                            mapbox_style="open-street-map")

#change the price legend
geo_fig.for_each_trace(lambda t: t.update(name = price_legend[t.name],
                                          legendgroup = price_legend[t.name],
                                          hovertemplate = t.hovertemplate.replace(t.name, price_legend[t.name])
                                         )
                      )

This scatter_mapbox visualisation gives the following observations:<br>
1. Properties below the price group of <= 1.868 million made up the majority of the dataset.
2. Properties are more densly packed within and around the city center. Refering to section 2.1.3. it should be properties within 20 km of CBD.
3. Interestingly, property prices beginning from 1.868 millions tends to cluster around the region East of Melbourne. As property prices increases, those properties only reside in East Melbourne.
4. The number of high valued property also decreases as the property prices increases.
5. Properties of price above 3.651 million are usually found within the city of Boroondara.
6. This visualisation gets difficult to infer for properties valued above 6.325 million. A disadvantage to look at where the outliers are.

### 2.1.4. Percentage of each property type

#### Earlier in section 2.1.3., we see that lower property prices made up majority of this dataset. We create a piechart to further explore which property type makes this observation true.

In [21]:
house_type_fig = px.pie(melb_house_price_df, values="Price", names="Type",
                        title="Proportion of Property Types in Melbourne",
                        hole=0.3)

house_type_fig.show()

- Type h properties stands at 80% of this dataset!
- As this dataset is populated with all sub-categories of type h (house, cottage, villa, semi, terrace) just as "h", it will be helpful if this type h category can be further split up to reduce the current imbalance.

### 2.1.5. Housing Facilities

#### We all know that property prices increase with more spacious house and more rooms and carspot (carpark). But we can try to visualise, for Melbourne, having which facility pushes the property prices up further more.

#### create a new dataframe to hold the data for this section's visualisation.

In [22]:
prop_facil_df = melb_house_price_df[["Rooms","Price","Bathroom","Car","Landsize"]]
prop_facil_df.head(3)

Rooms    Price  Bathroom  Car  Landsize
0      2  1480000         1  1.0       202
1      2  1035000         1  0.0       156
2      3  1465000         2  0.0       134

#### visualise with the newly created dataframe - say we further visualise in 4 portions.
- The steeper the gradient, the greater the linear relationship it is between house price and the feature we are going to compare.

In [23]:
# visualise rooms facility
prop_facil_fig_rm = px.scatter(prop_facil_df, x='Rooms', y="Price", color="Price", log_y=True,
                               trendline="ols", title="Effects of Property Price for No. of Rooms",
                               labels= {"Price":"House Price", "Rooms":"No. Rooms"},
                               color_continuous_scale=[(0, "red"), (0.5, "green"), (1, "blue")])

prop_facil_fig_rm.show()

In [24]:
# visualise bathroom facility
prop_facil_fig_bathrm = px.scatter(prop_facil_df, x='Bathroom', y="Price", color="Price", log_y=True,
                                   trendline="ols", title="Effects of Property Price for No. of Bathrooms",
                                   labels= {"Price":"House Price", "Car":"No. of Bathrooms"},
                                   color_continuous_scale=[(0, "red"), (0.5, "green"), (1, "blue")])

prop_facil_fig_bathrm.show()

In [25]:
# visualise carspots facility
prop_facil_fig_car = px.scatter(prop_facil_df, x='Car', y="Price", color="Price", log_y=True,
                                trendline="ols", title="Effects of Property Price for No. of Carspots",
                                labels= {"Price":"House Price", "Car":"No. of Carspots"},
                                color_continuous_scale=[(0, "red"), (0.5, "green"), (1, "blue")])

prop_facil_fig_car.show()

In [26]:
# visualise landsize area
prop_facil_fig_area = px.scatter(prop_facil_df, x='Price', y="Landsize", color="Price", log_x=True, log_y=True,
                                 trendline="ols", title="Effects of Property Price for Landsize",
                                 labels= {"Price":"House Price", "Landsize":"House Landsize"},
                                 color_continuous_scale=[(0, "red"), (0.5, "green"), (1, "blue")])

prop_facil_fig_area.show()

#### Summary for 2.1.5. Housing Facilities

In [27]:
prop_facil_fig_rm_results = px.get_trendline_results(prop_facil_fig_rm).px_fit_results.iloc[0]
print(f"Gradient (Rooms): {prop_facil_fig_rm_results.params[1]}")

prop_facil_fig_bathrm_results = px.get_trendline_results(prop_facil_fig_bathrm).px_fit_results.iloc[0]
print(f"Gradient (Bathroom): {prop_facil_fig_bathrm_results.params[1]}")

prop_facil_fig_car_results = px.get_trendline_results(prop_facil_fig_car).px_fit_results.iloc[0]
print(f"Gradient (Carspots): {prop_facil_fig_car_results.params[1]}")

prop_facil_fig_area_results = px.get_trendline_results(prop_facil_fig_area).px_fit_results.iloc[0]
print(f"Gradient (Landsize): {prop_facil_fig_area_results.params[1]}")

Gradient (Rooms): 332203.94464775745
Gradient (Bathroom): 431657.4509844481
Gradient (Carspots): 158848.56211501168
Gradient (Landsize): 0.0002341268834544941


- No. of bathrooms has the greatest influence in terms of property prices. This could be linked with the underlying cost where there could be more materials to use and labour work during the constructions of the bathrooms.
- No. of rooms has the second highest influence in terms of property prices.
- Carspots and Landsize are having weaker influence to property prices.

### 2.1.6 Geopolitical Influence

#### Sometimes, area with greater political influence affects property prices. However, with no political knowledge for the Melbourne city we can only make obeservation based on the values in this dataset.

#### create a new dataframe to hold the columns for this visualisation.

In [28]:
# only taking features with possible geopolitical relations
geopol_df = melb_house_price_df[["Type","Price","CouncilArea","Regionname","Propertycount"]]
geopol_df.head(3)

Type    Price CouncilArea             Regionname  Propertycount
0    h  1480000       Yarra  Northern Metropolitan           4019
1    h  1035000       Yarra  Northern Metropolitan           4019
2    h  1465000       Yarra  Northern Metropolitan           4019

#### visualise using a treemap as we can see some heirarchical relation between the columns.

However treemap is unable to handle null values. Only "CouncilArea" column is having null values. To allow the dataset to stay true, we temporarily replace the null values with the value of "unknown". 

In [29]:
geopol_df["CouncilArea"].fillna("unknown", inplace=True)

In [30]:
geopol_fig = px.treemap(geopol_df, path=[px.Constant("Melbourne"),"Regionname","CouncilArea","Type"],
                        values="Price",color="Price", height=800, hover_name="Type",
                        labels={"Price":"Prices in $"}, color_continuous_scale="earth",
                        title="Melbourne Property Price by Metropolitcan Region")

geopol_fig.data[0].hovertemplate = '<b>%{label}</b><br>%{value}'
geopol_fig.show()

- The Southern Metropolitan has shown the highest property sales transacted.
- All metropolitan has their own unknown council area and some are quite significant. Even though, there were originally 1369 missing values, which stands about 10% of the dataset, when added up its quite a sum. If wrongly computed, it can give a wrong impression. Below a pie chart illustrate the proportion of "unknown" council area.

In [31]:
council_area_fig = px.pie(geopol_df, values="Price", names="CouncilArea",
                          height=700, width=900, hole=0.3,
                          title="11.1% of Unknown Property Sales Transaction!")

council_area_fig.show()

In [32]:
melb_house_price_df.head()

Suburb           Address  Rooms Type    Price Method SellerG     Date  \
0  Abbotsford      85 Turner St      2    h  1480000      S     NaN  3/12/16   
1  Abbotsford   25 Bloomburg St      2    h  1035000      S  Biggin   4/2/16   
2  Abbotsford      5 Charles St      3    h  1465000     SP  Biggin   4/3/17   
3  Abbotsford  40 Federation La      3    h   850000     PI  Biggin   4/3/17   
4  Abbotsford       55a Park St      4    h  1600000     VB  Nelson   4/6/16   

   Distance  Postcode  Bedroom2  Bathroom  Car  Landsize  BuildingArea  \
0       2.5      3067         2         1  1.0       202           NaN   
1       2.5      3067         2         1  0.0       156          79.0   
2       2.5      3067         3         2  0.0       134         150.0   
3       2.5      3067         3         2  1.0        94           NaN   
4       2.5      3067         3         1  2.0       120         142.0   

   YearBuilt CouncilArea  Lattitude  Longtitude             Regionname  \
0        NaN       Yarra   -37.7996    144.9984  Northern Metropolitan   
1     1900.0       Yarra   -37.8079    144.9934  Northern Metropolitan   
2     1900.0       Yarra   -37.8093    144.9944  Northern Metropolitan   
3        NaN       Yarra   -37.7969    144.9969  Northern Metropolitan   
4     2014.0       Yarra   -37.8072    144.9941  Northern Metropolitan   

   Propertycount  
0           4019  
1           4019  
2           4019  
3           4019  
4           4019

## 2.2. Finding out null values

With a greater understanding and sense in the dataset through visualisation, we move on to data cleaning part.

In [33]:
# list out features with null values
melb_house_price_df.isnull().sum()

Suburb              0
Address             0
Rooms               0
Type                0
Price               0
Method              0
SellerG             1
Date                0
Distance            0
Postcode            0
Bedroom2            0
Bathroom            0
Car                62
Landsize            0
BuildingArea     6450
YearBuilt        5375
CouncilArea      1369
Lattitude           0
Longtitude          0
Regionname          0
Propertycount       0
dtype: int64

<b>Features with null values:</b>
1. SellerG
2. Car
3. BuildingArea
4. YearBuilt
5. Council Area

### 2.2.1. Handling null values - "SellerG"

<b>Find out the number of property agent this dataset has.</b>

In [34]:
# using unique() to list out all agents name and use .shape to count how many agents are there
num_of_property_agent = melb_house_price_df.SellerG.unique().shape[0]

# print out the results
print(f"There are {num_of_property_agent} property agents in this dataset.")

There are 269 property agents in this dataset.


<b>Take away that 1 particular row with null value in "SellerG"</br>

In [35]:
melb_house_price_df = melb_house_price_df[melb_house_price_df["SellerG"].notna()]

This [article](https://towardsdatascience.com/two-pandas-tricks-i-wish-id-known-earlier-60af0a049735) explains why `.notna()` is better than `.dropna()`.
Credits to [Liad Pollak Zuckerman](https://medium.com/@pollakliad) for the interesting insight!

In [36]:
melb_house_price_df.SellerG.isnull().sum()

0

### 2.2.2. Handling null values - "Car"

#### using statistical imputation method for missing values in "Car".

We find the most frequent value (no. carspots) within the "Car" column.

In [37]:
melb_house_price_df["Car"].mode()

0    2.0
dtype: float64

In [38]:
melb_house_price_df["Car"] = melb_house_price_df["Car"].fillna(melb_house_price_df["Car"].mode()[0])

In [39]:
melb_house_price_df.Car.isnull().sum()

0

# 3. Feature Engineering

# 4. Model Building

# 5. Generate and Export Prediction from Final Model